In [136]:
import MeCab
from collections import defaultdict
import pandas as pd
import MeCab
import ipadic
from collections import Counter
import re
import matplotlib.pyplot as plt
import numpy as np
import japanize_matplotlib

In [137]:
data=pd.read_csv("./朝ポキ出演者 共同編集用 スプレッドシート - ニュースの現場から.csv")
data

omny.fm へのリンク  \
0                    https://omny.fm/shows/asahi/9-ny-1   
1                      https://omny.fm/shows/asahi/9-ny   
2     https://omny.fm/shows/asahi/28bbd9d5-fe0e-4a05...   
3     https://omny.fm/shows/asahi/c4b6b21d-f0c6-4bfe...   
4     https://omny.fm/shows/asahi/9afa3ecf-29ff-4faa...   
...                                                 ...   
1440                   https://omny.fm/shows/asahi/1298   
1441                   https://omny.fm/shows/asahi/1299   
1442                  https://omny.fm/shows/asahi/1300a   
1443                   https://omny.fm/shows/asahi/1301   
1444                   https://omny.fm/shows/asahi/1302   

                                   日付                                    タイトル  \
0     Thu, 06 Aug 2020 02:06:00 +0000    #1 ニューヨーク　感染爆発、でも9割が対応支持　NY覆う「戦時の空気」   
1     Sat, 08 Aug 2020 02:00:00 +0000       #2 ローマ　奔放イタリア、コロナで見せた従順　マフィアのボスも…   
2     Sun, 09 Aug 2020 02:00:00 +0000     #3 モスクワ①　医師が事実を訴えると、警察くるロシア　プーチン氏は…   
3     Sun, 09 Aug 2020 02:00:00 +0000    #4 モスクワ②　緊急事態宣言、出さないプーチン大統領　抗議もバーチャル   
4     Sun, 09 Aug 2020 02:01:00 +0000      #5 モスクワ③　実は欧米より制限ゆるかったロシア　日本を見て驚いた   
...                               ...                                     ...   
1440  Wed, 18 Oct 2023 19:00:00 +0000  イスラエル・パレスチナ問題を徹底解説　何が、なぜ、どうなっている #1298   
1441  Thu, 19 Oct 2023 19:00:00 +0000           中国の国防相はなぜ消えた　魚の禁輸も外交カード #1299   
1442  Fri, 20 Oct 2023 19:00:00 +0000    始まった処理水の海洋放出　福島との「約束」、政府は果たしたか #1300   
1443  Sat, 21 Oct 2023 19:00:00 +0000    必読！　あなたもテロリストになり得るし、カルトにはまり得る訳 #1301   
1444  Sun, 22 Oct 2023 19:00:00 +0000       時計もねェ　時刻表もねェ　スマホがねェとどうなっちゃう #1302   

      コメント           MC                 出演者1 出演者2 出演者3  音源編集  \
0      NaN         神田大介        藤原学思,ニューヨーク支局  NaN  NaN   NaN   
1      NaN         神田大介          河原田慎一,ローマ支局  NaN  NaN   NaN   
2      NaN         神田大介          石橋亮介,モスクワ支局  NaN  NaN   NaN   
3      NaN         神田大介          石橋亮介,モスクワ支局  NaN  NaN   NaN   
4      NaN         神田大介          石橋亮介,モスクワ支局  NaN  NaN   NaN   
...    ...          ...                  ...  ...  ...   ...   
1440   NaN         神田大介           高野遼,アメリカ総局  NaN  NaN   杢田光   
1441   NaN         神田大介             冨名腰隆,経済部  NaN  NaN   向平真   
1442   NaN         飯島啓史         福地慶太郎,科学みらい部  NaN  NaN  飯島啓史   
1443   NaN  竹田真志夫,高知総局長  吉村昇洋さん,広島市の曹洞宗普門寺住職  NaN  NaN  久保智祥   
1444   NaN          NaN                  NaN  NaN  NaN   NaN   

     備考・メモ・作業された方のお名前(ハンドルネーム可)  
0                 いーむ（em_em000）  
1                 いーむ（em_em000）  
2                 いーむ（em_em000）  
3                 いーむ（em_em000）  
4                 いーむ（em_em000）  
...                         ...  
1440                        かにこ  
1441                      koike  
1442                        かにこ  
1443                      koike  
1444                        NaN  

[1445 rows x 10 columns]

In [60]:
""" MC出演者がいない場合はNone,いる場合は出演者の所属を削除する関数 """
def speakerTakeOut(speaker):
    if (pd.isna(speaker)):
        return None
    else:
        speakerOnly=str(speaker.split(",")[0])
        return speakerOnly
""" 既存のリストに出演者とタイトルの辞書型を追加する関数 """    
def podDict(lists,title,member):
    dic={"title":title,"performer":member}
    lists.append(dic)
    return lists

""" タイトルを読み込み数以外の名詞を出力する関数 """
def collectWords(titleName):
    m = MeCab.Tagger(ipadic.MECAB_ARGS)
    words_lines = m.parse(titleName).split('\n')
    parsed_words = []
    for  word_line in words_lines:
        parsed_words.append(re.split('[\t,]', word_line))
    #名詞・一般に該当する単語をリストに格納
    words = []
    for parsed_word in parsed_words:
        if (    parsed_word[0] not in ('EOS', '') 
            and parsed_word[1] == '名詞'
            and parsed_word[2] != '数'):
            words.append(parsed_word[0])

In [142]:
#データから出演者データのみを切り取り
data["出演者1"]=data["出演者1"].apply(speakerTakeOut)
data["出演者2"]=data["出演者2"].apply(speakerTakeOut)
data["出演者3"]=data["出演者3"].apply(speakerTakeOut)
data["MC"]=data["MC"].apply(speakerTakeOut)

In [141]:
#データを辞書型にして「MC,タイトル」「出演者,タイトル」の辞書型データにしてリスト化
podcasts=[]
for title,p1,p2,p3,mc in zip(data["タイトル"],data["出演者1"],data["出演者2"],data["出演者3"],data["MC"]):
    podDict(podcasts,title,mc)
    if (pd.isna(p3)==False):
        podDict(podcasts,title,p1)
        podDict(podcasts,title,p2)
        podDict(podcasts,title,p3)
    elif (pd.isna(p2==False)):
        podDict(podcasts,title,p1)
        podDict(podcasts,title,p2)
    else:
        podDict(podcasts,title,p1)
podcasts

[{'title': '#1 ニューヨーク\u3000感染爆発、でも9割が対応支持\u3000NY覆う「戦時の空気」',
  'performer': '神田大介'},
 {'title': '#1 ニューヨーク\u3000感染爆発、でも9割が対応支持\u3000NY覆う「戦時の空気」',
  'performer': '藤原学思'},
 {'title': '#2 ローマ\u3000奔放イタリア、コロナで見せた従順\u3000マフィアのボスも…', 'performer': '神田大介'},
 {'title': '#2 ローマ\u3000奔放イタリア、コロナで見せた従順\u3000マフィアのボスも…',
  'performer': '河原田慎一'},
 {'title': '#3 モスクワ①\u3000医師が事実を訴えると、警察くるロシア\u3000プーチン氏は…',
  'performer': '神田大介'},
 {'title': '#3 モスクワ①\u3000医師が事実を訴えると、警察くるロシア\u3000プーチン氏は…',
  'performer': '石橋亮介'},
 {'title': '#4 モスクワ②\u3000緊急事態宣言、出さないプーチン大統領\u3000抗議もバーチャル',
  'performer': '神田大介'},
 {'title': '#4 モスクワ②\u3000緊急事態宣言、出さないプーチン大統領\u3000抗議もバーチャル',
  'performer': '石橋亮介'},
 {'title': '#5 モスクワ③\u3000実は欧米より制限ゆるかったロシア\u3000日本を見て驚いた',
  'performer': '神田大介'},
 {'title': '#5 モスクワ③\u3000実は欧米より制限ゆるかったロシア\u3000日本を見て驚いた',
  'performer': '石橋亮介'},
 {'title': '#6 シンガポール①\u3000ロボット犬がにらんでる\u3000「管理社会」の理詰めコロナ策',
  'performer': '神田大介'},
 {'title': '#6 シンガポール①\u3000ロボット犬がにらんでる\u3000「管理社会」の理詰めコロナ策',
  'performer': 

In [134]:
# ポッドキャストのタイトルと出演者データ

#メンバーごとに単語を抽出する
def collectWords(titleName):
    m = MeCab.Tagger(ipadic.MECAB_ARGS)
    words_lines = m.parse(titleName).split('\n')
    parsed_words = []
    for  word_line in words_lines:
        parsed_words.append(re.split('[\t,]', word_line))
    #名詞・一般に該当する単語をリストに格納
    words = []
    for parsed_word in parsed_words:
        if (    parsed_word[0] not in ('EOS', '') 
            and parsed_word[1] == '名詞'
            and parsed_word[2] != '数'):
            words.append(parsed_word[0])
    """
    for parsed_word in parsed_words:
        if (    parsed_word[0] not in ('EOS', '') 
            and parsed_word[1] == '名詞'
            and parsed_word[2] == '一般'):
            words.append(parsed_word[0])
    for parsed_word in parsed_words:
        if (    parsed_word[0] not in ('EOS', '') 
            and parsed_word[1] == '名詞'
            and parsed_word[2] == "固有名詞"):
            words.append(parsed_word[0])
    for parsed_word in parsed_words:
        if (    parsed_word[0] not in ('EOS', '') 
            and parsed_word[1] == '名詞'
            and parsed_word[2] == "サ変接続"):
            words.append(parsed_word[0])
    """
    print(words)
    return words

# MeCabの初期化
""" 
# 出演者ごとの単語集計
performer_words = defaultdict(list)

K_parsed_words = []
K_words = []
for podcast in podcasts:
    # タイトルから単語を分離
    words_lines = m.parse(podcast["title"]).split('\n')
    parsed_words = []
    words = []
    for  word_line in words_lines:
        K_parsed_words.append(re.split('[\t,]', word_line))

    #念の為分析をもう一度
K_parsed = tagger.parse(titleAll)
#分析データを改行ごとに切り取り
K_parsed_lines = K_parsed.split('\n')

#処理に使うリストを作成
K_parsed_words = []
K_words = []
 
#各行のタブ（\t）を除去
for K_parsed_line in K_parsed_lines:
    K_parsed_words.append(re.split('[\t,]', K_parsed_line))
 
#名詞・一般に該当する単語をリストに格納
for K_parsed_word in K_parsed_words:
    if (    K_parsed_word[0] not in ('EOS', '') 
        and K_parsed_word[1] == '名詞'
        and K_parsed_word[2] == '固有名詞'):
        
            K_words.append(K_parsed_word[0])
"""
performer_words = defaultdict(list)
for podcast in podcasts:
        # 単語を出演者データに追加
    print(podcast["performer"],podcast["title"])
    performer_words[podcast["performer"]].extend(collectWords(podcast["title"]))

"""
def recommend_keywords(performer):
    # 出演者の単語リストを取得
    words = performer_words.get(performer, [])
    
    # 単語の頻度を集計
    word_counts = defaultdict(int)
    for word in words:
        word_counts[word] += 1
    
    # 頻度順にソートして上位5つの単語を返す
    recommended = sorted(word_counts.items(), key=lambda x: x[1], reverse=True)[:5]
    
    return [word for word, _ in recommended]

# 出演者名を入力しておすすめの検索ワードを出力
print(recommend_keywords("石原孝"))
"""

神田大介 #1 ニューヨーク　感染爆発、でも9割が対応支持　NY覆う「戦時の空気」
['ニューヨーク', '感染', '爆発', '割', '対応', '支持', 'NY', '戦時', '空気']
藤原学思 #1 ニューヨーク　感染爆発、でも9割が対応支持　NY覆う「戦時の空気」
['ニューヨーク', '感染', '爆発', '割', '対応', '支持', 'NY', '戦時', '空気']
神田大介 #2 ローマ　奔放イタリア、コロナで見せた従順　マフィアのボスも…
['ローマ', '奔放', 'イタリア', 'コロナ', '従順', 'マフィア', 'ボス']
河原田慎一 #2 ローマ　奔放イタリア、コロナで見せた従順　マフィアのボスも…
['ローマ', '奔放', 'イタリア', 'コロナ', '従順', 'マフィア', 'ボス']
神田大介 #3 モスクワ①　医師が事実を訴えると、警察くるロシア　プーチン氏は…
['モスクワ', '医師', '事実', '警察', 'ロシア', 'プーチン', '氏']
石橋亮介 #3 モスクワ①　医師が事実を訴えると、警察くるロシア　プーチン氏は…
['モスクワ', '医師', '事実', '警察', 'ロシア', 'プーチン', '氏']
神田大介 #4 モスクワ②　緊急事態宣言、出さないプーチン大統領　抗議もバーチャル
['モスクワ', '緊急', '事態', '宣言', 'プーチン', '大統領', '抗議', 'バーチャル']
石橋亮介 #4 モスクワ②　緊急事態宣言、出さないプーチン大統領　抗議もバーチャル
['モスクワ', '緊急', '事態', '宣言', 'プーチン', '大統領', '抗議', 'バーチャル']
神田大介 #5 モスクワ③　実は欧米より制限ゆるかったロシア　日本を見て驚いた
['モスクワ', '欧米', '制限', 'ロシア', '日本']
石橋亮介 #5 モスクワ③　実は欧米より制限ゆるかったロシア　日本を見て驚いた
['モスクワ', '欧米', '制限', 'ロシア', '日本']
神田大介 #6 シンガポール①　ロボット犬がにらんでる　「管理社会」の理詰めコロナ策
['シンガポール', 'ロボット', '犬', '管理', '社会', '理詰め', 'コロナ', '策']
西村宏

'\ndef recommend_keywords(performer):\n    # 出演者の単語リストを取得\n    words = performer_words.get(performer, [])\n    \n    # 単語の頻度を集計\n    word_counts = defaultdict(int)\n    for word in words:\n        word_counts[word] += 1\n    \n    # 頻度順にソートして上位5つの単語を返す\n    recommended = sorted(word_counts.items(), key=lambda x: x[1], reverse=True)[:5]\n    \n    return [word for word, _ in recommended]\n\n# 出演者名を入力しておすすめの検索ワードを出力\nprint(recommend_keywords("石原孝"))\n'

In [114]:
performer_words["神田大介"]

['戦時',
 '空気',
 'コロナ',
 '従順',
 'ボス',
 '医師',
 '警察',
 '事態',
 'プーチン',
 '大統領',
 'バーチャル',
 'ロボット',
 '社会',
 '理詰め',
 'コロナ',
 '飯場',
 'コロナ',
 '政府',
 'カード',
 '状況',
 '外',
 'オリンピック',
 'コロナ',
 '効果',
 '驚き',
 'データ',
 'サンパウロ',
 'スラム',
 '不可避',
 'サンパウロ',
 'トロピカル',
 'トランプ',
 '福音',
 '影',
 'コロナ',
 '水',
 '病院',
 '都知事',
 'アラート',
 '都知事',
 '五輪',
 'コロナ',
 '本当',
 '都知事',
 '都知事',
 '理由',
 '都民',
 'ファースト',
 '都知事',
 '本人',
 '人事',
 '都知事',
 '人気',
 'マスコミ',
 '責任',
 '首相',
 '夫',
 '日記',
 '最後',
 '一言',
 '闇',
 '首相',
 '政府',
 '答え',
 '日常',
 '笑顔',
 'コロナ',
 'コロナ',
 '世界',
 '責任',
 '記事',
 '舞台裏',
 '血',
 '血',
 '宿縁',
 '自分',
 '状態',
 '手法',
 'コロナ',
 '経済',
 '内戦',
 '国',
 'コロナ',
 '現状',
 '辞意',
 '内幕',
 '官邸',
 '記者',
 'コロナ',
 '上司',
 '患者',
 '記者',
 '首相',
 '単独',
 '首相',
 '棒読み',
 'マスコミ',
 '責任',
 '記者',
 'クラブ',
 'けんか',
 '総裁',
 '標的',
 '未婚',
 '母',
 '権利',
 '理由',
 '人',
 '菅',
 '政権',
 '党人',
 '因縁',
 'ダイソン',
 '人工',
 'コロナ',
 'スキャンダル',
 '教授',
 'パンツ',
 '逆境',
 'コロナ',
 '王室',
 'メーガン',
 'ブーイング',
 '拠点',
 'コロナ',
 '一つ',
 '理由',
 'マンション',
 '村',
 'コロナ',
 '技能',
 'SNS',
 '暴力',
 '動

In [106]:
def collectWords(title,member):
    m = MeCab.Tagger(ipadic.MECAB_ARGS)
    words_lines = m.parse(title).split('\n')
    parsed_words = []
    for  word_line in words_lines:
        parsed_words.append(re.split('[\t,]', word_line))
    
    #名詞・一般に該当する単語をリストに格納
    words = []
    for parsed_word in parsed_words:
        if (    parsed_word[0] not in ('EOS', '') 
            and parsed_word[1] == '名詞'
            and parsed_word[2] == '一般'):
            
            words.append(parsed_word[0])
    for parsed_word in parsed_words:
        if (    parsed_word[0] not in ('EOS', '') 
            and parsed_word[1] == '名詞'
            and parsed_word[2] == '固有名詞'):
            
            words.append(parsed_word[0])
    print(words,member)
    return words

In [107]:
title="頻度順にソートして上位5つの単語を返す"
collectWords(title,"神田大介")

['頻度', 'ソート', '上位', '単語'] 神田大介


['頻度', 'ソート', '上位', '単語']

In [89]:
def collectWords(title,member):
    m = MeCab.Tagger(ipadic.MECAB_ARGS)
    words_lines = m.parse(title).split('\n')
    parsed_words = []
    for  word_line in words_lines:
        parsed_words.append(re.split('[\t,]', word_line))
    #名詞・一般に該当する単語をリトに格納
    
    words = []
    for parsed_word in parsed_words:
        if (    parsed_word[0] not in ('EOS', '') 
            and parsed_word[1] == '名詞'
            and parsed_word[2] == '一般'):
            
            words.append(parsed_word[0])
    return words

In [90]:
collectWords("ニューヨーク　感染爆発、でも9割が対応支持　NY覆う「戦時の空気」","神田大介")


['戦時', '空気']

In [135]:
m.parse("ニューヨーク　感染爆発、でも9割が対応支持　NY覆う「戦時の空気」").split('\n')

['ニューヨーク\t名詞,固有名詞,地域,一般,*,*,ニューヨーク,ニューヨーク,ニューヨーク',
 '\u3000\t記号,空白,*,*,*,*,\u3000,\u3000,\u3000',
 '感染\t名詞,サ変接続,*,*,*,*,感染,カンセン,カンセン',
 '爆発\t名詞,サ変接続,*,*,*,*,爆発,バクハツ,バクハツ',
 '、\t記号,読点,*,*,*,*,、,、,、',
 'でも\t接続詞,*,*,*,*,*,でも,デモ,デモ',
 '9\t名詞,数,*,*,*,*,*',
 '割\t名詞,接尾,助数詞,*,*,*,割,ワリ,ワリ',
 'が\t助詞,格助詞,一般,*,*,*,が,ガ,ガ',
 '対応\t名詞,サ変接続,*,*,*,*,対応,タイオウ,タイオー',
 '支持\t名詞,サ変接続,*,*,*,*,支持,シジ,シジ',
 '\u3000\t記号,空白,*,*,*,*,\u3000,\u3000,\u3000',
 'NY\t名詞,固有名詞,組織,*,*,*,*',
 '覆う\t動詞,自立,*,*,五段・ワ行促音便,基本形,覆う,オオウ,オオウ',
 '「\t記号,括弧開,*,*,*,*,「,「,「',
 '戦時\t名詞,一般,*,*,*,*,戦時,センジ,センジ',
 'の\t助詞,連体化,*,*,*,*,の,ノ,ノ',
 '空気\t名詞,一般,*,*,*,*,空気,クウキ,クーキ',
 '」\t記号,括弧閉,*,*,*,*,」,」,」',
 'EOS',
 '']

In [43]:
performer_words

defaultdict(list,
            {'神田大介': ['#',
              '記号,一般,*,*,*,*,*',
              '1',
              '名詞,数,*,*,*,*,*',
              'ニューヨーク',
              '名詞,固有名詞,地域,一般,*,*,ニューヨーク,ニューヨーク,ニューヨーク',
              '記号,空白,*,*,*,*,',
              ',',
              ',',
              '感染',
              '名詞,サ変接続,*,*,*,*,感染,カンセン,カンセン',
              '爆発',
              '名詞,サ変接続,*,*,*,*,爆発,バクハツ,バクハツ',
              '、',
              '記号,読点,*,*,*,*,、,、,、',
              'でも',
              '接続詞,*,*,*,*,*,でも,デモ,デモ',
              '9',
              '名詞,数,*,*,*,*,*',
              '割',
              '名詞,接尾,助数詞,*,*,*,割,ワリ,ワリ',
              'が',
              '助詞,格助詞,一般,*,*,*,が,ガ,ガ',
              '対応',
              '名詞,サ変接続,*,*,*,*,対応,タイオウ,タイオー',
              '支持',
              '名詞,サ変接続,*,*,*,*,支持,シジ,シジ',
              '記号,空白,*,*,*,*,',
              ',',
              ',',
              'NY',
              '名詞,固有名詞,組織,*,*,*,*',
              '覆う',
              '動詞,自立,*,*,五段・ワ行

[',', '記号,一般,*,*,*,*,*', '名詞,数,*,*,*,*,*', '#', 'EOS']

### 参考出演者集計

In [46]:
testData1=data.groupby(["MC"]).agg({"日付":"count"}).reset_index()
testData1.sort_values("日付",ascending=False)
testData1.head(50)

MC   日付
0                               中島信也    1
1                               中程雄平    2
2                 中程雄平,大阪本社コンテンツ編成本部    3
3   久保智祥,大阪本社コンテンツ編成本部,大阪音声チーム,天台宗僧侶    2
4                 久保智祥,大阪音声チーム,天台宗僧侶    6
5                 久保智祥,大阪音声チーム・天台宗僧侶    6
6                                井岡諒    3
7                                今永諒   15
8                               仲程雄平   14
9                 仲程雄平,大阪本社コンテンツ編成本部   17
10                             伊藤あずさ    7
11                             加地ゆうき    7
12                               向平真   33
13                            哲夫,笑い飯   51
14                              堀江麻友   10
15                              大野由衣    2
16                    大野由衣,朝デジ事業センター    1
17                              安田桂子   24
18                    安田桂子,コンテンツ編成本部   14
19                              宮沢賢一   36
20                              尾崎千裕    4
21                      尾崎千裕,大阪本社文化部    7
22                      尾崎千裕,大阪生活文化部    3
23                               岸上渉   55
24                 岸上渉,大阪本社コンテンツ編成本部   34
25                               影山遼    2
26                              木下広大   24
27                         木下広大,大阪本社    2
28                               杢田光   12
29                              桂佐ん吉    1
30                               桂吉弥   24
31                            桂吉弥,芸人   18
32                              橋下佳奈    1
33                              橋本佳奈    2
34                               水野梓   18
35                   水野梓,withnews編集長   11
36                     河合真美江,大阪本社編集局    4
37                        玉置太郎,大阪社会部    1
38                       田中ゑれ奈,大阪文化部    1
39                               真田嶺   13
40                     真田嶺,コンテンツ編成本部    2
41                         真田嶺,音声チーム    2
42                              神田大介  604
43                     神田大介,音声ディレクター    3
44           神田大介,音声ディレクター,コンテンツ編成本部  228
45                               神谷毅    2
46                         秋山訓子,編集委員   28
47                             竹田真志夫   11
48                   竹田真志夫,大阪文化部,デスク    8
49                    竹田真志夫,大阪文化部デスク   18

In [ ]:


# ポッドキャストのタイトルと出演者データ
podcasts = [
    {"title": "タイトル1", "performers": ["出演者A", "出演者B"]},
    {"title": "タイトル2", "performers": ["出演者C"]},
    # 他のポッドキャストデータ...
]

# MeCabの初期化
m = MeCab.Tagger("-Owakati")

# 出演者ごとの単語集計
performer_words = defaultdict(list)

for podcast in podcasts:
    # タイトルから単語を分離
    words = m.parse(podcast["title"]).split()
    
    for performer in podcast["performers"]:
        # 単語を出演者データに追加
        performer_words[performer].extend(words)

def recommend_keywords(performer):
    # 出演者の単語リストを取得
    words = performer_words.get(performer, [])
    
    # 単語の頻度を集計
    word_counts = defaultdict(int)
    for word in words:
        word_counts[word] += 1
    
    # 頻度順にソートして上位5つの単語を返す
    recommended = sorted(word_counts.items(), key=lambda x: x[1], reverse=True)[:5]
    
    return [word for word, _ in recommended]

# 出演者名を入力しておすすめの検索ワードを出力
print(recommend_keywords("出演者A"))
